# Install the required packages and dependencies

In [3]:
%pip install datasets wandb note_seq soundfile jiwer pesq
%pip install -U huggingface_hub accelerate
%pip install --no-cache-dir transformers sentencepiece
%pip install --upgrade pyfluidsynth

  Using cached wandb-0.16.4-py3-none-any.whl.metadata (10 kB)
  Using cached jiwer-3.0.3-py3-none-any.whl.metadata (2.6 kB)
  Using cached pesq-0.0.4.tar.gz (38 kB)
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Using cached click-8.1.7-py3-none-any.whl.metadata (3.0 kB)
  Using cached GitPython-3.1.42-py3-none-any.whl.metadata (12 kB)
  Using cached sentry_sdk-1.42.0-py2.py3-none-any.whl.metadata (9.8 kB)
  Using cached docker_pycreds-0.4.0-py2.py3-none-any.whl.metadata (1.8 kB)
  Using cached setproctitle-1.3.3-cp312-cp312-win_amd64.whl.metadata (10 kB)
  Using cached appdirs-1.4.4-py2.py3-none-any.whl.metadata (9.0 kB)
  Using cached protobuf-4.25.3-cp310-abi3-win_amd64.whl.metadata (541 bytes)
  Using cached rapidfuzz-3.6.2-cp312-cp312-win_amd64.whl.metadata (11 kB)
  Using cached gitdb-4.0.11-py3-none-any.whl.metadata (1.2 kB)
  Using cached smmap-5.0.1-py3-none-any.whl.metadata (4.3 kB)
Using cached wandb-0.16.4-py3-none-an

  error: subprocess-exited-with-error
  
  × python setup.py bdist_wheel did not run successfully.
  │ exit code: 1
  ╰─> [34 lines of output]
      c:\Users\liyak\anaconda3\envs\torch\Lib\site-packages\setuptools\__init__.py:80: _DeprecatedInstaller: setuptools.installer and fetch_build_eggs are deprecated.
      !!
      
              ********************************************************************************
              Requirements should be satisfied by a PEP 517 installer.
              If you are using pip, you can try `pip install --use-pep517`.
              ********************************************************************************
      
      !!
        dist.fetch_build_eggs(dist.setup_requires)
      running bdist_wheel
      running build
      running build_py
      creating build
      creating build\lib.win-amd64-cpython-312
      creating build\lib.win-amd64-cpython-312\pesq
      copying pesq\_pesq.py -> build\lib.win-amd64-cpython-312\pesq
      copying

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [1]:
%pip install https://github.com/ludlows/python-pesq/archive/master.zip

     - 0 bytes ? 0:00:00
     - 6.2 kB ? 0:00:00
     - 34.2 kB 654.4 kB/s 0:00:00
     \ 97.1 kB 859.0 kB/s 0:00:00
     \ 204.9 kB 1.3 MB/s 0:00:00
     | 223.1 kB 1.0 MB/s 0:00:00
     | 223.1 kB 1.0 MB/s 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Running setup.py clean for pesq
Failed to build pesq
Note: you may need to restart the kernel to use updated packages.


  error: subprocess-exited-with-error
  
  × python setup.py bdist_wheel did not run successfully.
  │ exit code: 1
  ╰─> [34 lines of output]
      c:\Users\liyak\anaconda3\envs\torch\Lib\site-packages\setuptools\__init__.py:80: _DeprecatedInstaller: setuptools.installer and fetch_build_eggs are deprecated.
      !!
      
              ********************************************************************************
              Requirements should be satisfied by a PEP 517 installer.
              If you are using pip, you can try `pip install --use-pep517`.
              ********************************************************************************
      
      !!
        dist.fetch_build_eggs(dist.setup_requires)
      running bdist_wheel
      running build
      running build_py
      creating build
      creating build\lib.win-amd64-cpython-312
      creating build\lib.win-amd64-cpython-312\pesq
      copying pesq\_pesq.py -> build\lib.win-amd64-cpython-312\pesq
      copying

# Import the packages

In [1]:
from huggingface_hub import notebook_login
from datasets import load_dataset
import wandb
from argparse import Namespace

import torch
from transformers import AutoTokenizer, PreTrainedTokenizerFast, PreTrainedTokenizer, AutoConfig, \
                        GPT2LMHeadModel, DataCollatorForLanguageModeling, Trainer, TrainingArguments, \
                        LogitsProcessorList, LogitsProcessor

from tokenizers import Tokenizer
from tokenizers.models import WordLevel
from tokenizers.pre_tokenizers import WhitespaceSplit
from tokenizers.trainers import WordLevelTrainer

from IPython.display import Audio
import numpy as np

# The below two package imports would require a dedicated cell. With a function called token_to_note_seq
import note_seq

c:\Users\liyak\anaconda3\envs\torch\Lib\site-packages\pydub\utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
  warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)


In [4]:
notebook_login()

In [5]:
wandb.login()

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Appending key for api.wandb.ai to your netrc file: C:\Users\liyak\.netrc


True

# Load the dataset and prepare the GPT-2 model with the required parameters

In [2]:
LANGUAGE = "english"
DATASET = f"okbenzene2002/{LANGUAGE}-dataset"
TOKENIZER = f"okbenzene2002/{LANGUAGE}-tokenizer"

In [3]:
data = load_dataset(DATASET, split='train')
dataset_split = data.train_test_split(test_size=0.25, shuffle=True)
sample = dataset_split['train']['text'][0]
sample

'PIECE_START TIME_SIGNATURE GENRE=OTHER TRACK_START INST=0 DENSITY=3 BAR_START NOTE_ON=51 NOTE_ON=75 TIME_DELTA=2.0 NOTE_ON=55 TIME_DELTA=1.0 NOTE_OFF=75 TIME_DELTA=1.0 NOTE_OFF=55 NOTE_ON=54 TIME_DELTA=2.0 NOTE_OFF=54 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 NOTE_ON=54 TIME_DELTA=2.0 NOTE_OFF=54 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 NOTE_ON=54 TIME_DELTA=2.0 NOTE_OFF=54 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=51 NOTE_OFF=55 BAR_END BAR_START NOTE_ON=53 NOTE_ON=50 TIME_DELTA=2.0 NOTE_OFF=53 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 NOTE_ON=53 TIME_DELTA=2.0 NOTE_OFF=53 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=50 NOTE_OFF=55 NOTE_ON=51 NOTE_ON=48 TIME_DELTA=2.0 NOTE_OFF=51 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 NOTE_ON=51 TIME_DELTA=2.0 NOTE_OFF=51 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=48 NOTE_OFF=55 BAR_END BAR_START NOTE_ON=50 NOTE_ON=47 TIME_DELTA=2.0 NOTE_OFF=50 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 NOTE_ON=50 TIME_DELTA=2.0 NOTE_OFF=50 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 NOTE_ON=50 NOTE_ON=78 TIME_DEL

## Load the custom trained tokenizer

In [4]:
tokenizer = AutoTokenizer.from_pretrained(TOKENIZER)
tokenizer.add_special_tokens({'pad_token': '[PAD]'})
print("Length of tokenizer: ", len(tokenizer))
tokenizer

Length of tokenizer:  2052


PreTrainedTokenizerFast(name_or_path='okbenzene2002/english-tokenizer', vocab_size=2052, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	3: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	4: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}

## Create tokenized dataset from the custom trained tokenizer

In [5]:
# A default context length value that determines the lenght of tokens to be
context_length = 2048

def tokenize(texts):
    tokens = tokenizer(texts['text'], truncation=True, max_length=context_length, padding=False)
    return {"input_ids": tokens['input_ids']}

tokenized_dataset = dataset_split.map(tokenize, batched=True, remove_columns=dataset_split['train'].column_names)
tokenized_dataset

Map:   0%|          | 0/2508 [00:00<?, ? examples/s]

Map:   0%|          | 0/837 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['input_ids'],
        num_rows: 2508
    })
    test: Dataset({
        features: ['input_ids'],
        num_rows: 837
    })
})

# GPT-2 Model Configuration and Training using Weights and Biases

* Language model's are trained on millions of records which makes them scalable for having better weights and biases at each level layer.

* These parameters can be used to train on the local machines with having to trouble for the system configurations.

In [6]:
# This GPT-2 model is used on larger datasets and
n_layer = 8
n_head = 8
n_embd = 512

config = AutoConfig.from_pretrained(
    "gpt2",
    vocab_size=len(tokenizer),
    n_positions=context_length,
    n_layer=n_layer,
    n_head=n_head,
    pad_token_id=tokenizer.pad_token_id,
    bos_token_id=tokenizer.bos_token_id,
    eos_token_id=tokenizer.eos_token_id,
    n_embd=n_embd
    )

model = GPT2LMHeadModel(config)
model

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(2052, 512)
    (wpe): Embedding(2048, 512)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-7): 8 x GPT2Block(
        (ln_1): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=512, out_features=2052, bias=False)
)

# Data Collator for creating a batch data

In [7]:
data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)
data_collator

DataCollatorForLanguageModeling(tokenizer=PreTrainedTokenizerFast(name_or_path='okbenzene2002/english-tokenizer', vocab_size=2052, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	3: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	4: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}, mlm=False, mlm_probability=0.15, pad_to_multi

# Fixing the model parameters and training the model

In [8]:
NOTE_LENGTH_16TH_120BPM = 0.25 * 60 / 120
BAR_LENGTH_120BPM = 4.0 * 60 / 120


def token_sequence_to_note(
    token_sequence,
    use_program=True,
    use_drums=True,
    instrument_mapper=None,
    only_piano=False,
):
    if isinstance(token_sequence, str):
        token_sequence = token_sequence.split()

    note_sequence = empty_note_sequence()

    # Render all notes.
    current_program = 1
    current_is_drum = False
    current_instrument = 0
    track_count = 0
    current_bar_index = 0
    current_time = 0
    current_notes = {}
    for token_index, token in enumerate(token_sequence):
        if token == "PIECE_START":
            pass
        elif token == "PIECE_END":
            print("The end.")
            break
        elif token == "TRACK_START":
            current_bar_index = 0
            track_count += 1
            pass
        elif token == "TRACK_END":
            pass
        elif token == "KEYS_START":
            pass
        elif token == "KEYS_END":
            pass
        elif token.startswith("KEY="):
            pass
        elif token.startswith("INST"):
            instrument = token.split("=")[-1]
            if instrument != "DRUMS" and use_program:
                if instrument_mapper is not None:
                    if instrument in instrument_mapper:
                        instrument = instrument_mapper[instrument]
                current_program = int(instrument)
                current_instrument = track_count
                current_is_drum = False
            if instrument == "DRUMS" and use_drums:
                current_instrument = 0
                current_program = 0
                current_is_drum = True
        elif token == "BAR_START":
            current_time = current_bar_index * BAR_LENGTH_120BPM
            current_notes = {}
        elif token == "BAR_END":
            current_bar_index += 1
            pass
        elif token.startswith("NOTE_ON"):
            pitch = int(token.split("=")[-1])
            note = note_sequence.notes.add()
            note.start_time = current_time
            note.end_time = current_time + 4 * NOTE_LENGTH_16TH_120BPM
            note.pitch = pitch
            note.instrument = current_instrument
            note.program = current_program
            note.velocity = 80
            note.is_drum = current_is_drum
            current_notes[pitch] = note
        elif token.startswith("NOTE_OFF"):
            pitch = int(token.split("=")[-1])
            if pitch in current_notes:
                note = current_notes[pitch]
                note.end_time = current_time
        elif token.startswith("TIME_DELTA"):
            delta = float(token.split("=")[-1]) * NOTE_LENGTH_16TH_120BPM
            current_time += delta
        elif token.startswith("DENSITY="):
            pass
        elif token == "[PAD]":
            pass
        else:
            # print(f"Ignored token {token}.")
            pass

    # Make the instruments right.
    instruments_drums = []
    for note in note_sequence.notes:
        pair = [note.program, note.is_drum]
        if pair not in instruments_drums:
            instruments_drums += [pair]
        note.instrument = instruments_drums.index(pair)

    if only_piano:
        for note in note_sequence.notes:
            if not note.is_drum:
                note.instrument = 0
                note.program = 0

    return note_sequence


def empty_note_sequence(qpm=120.0, total_time=0.0):
    note_sequence = note_seq.protobuf.music_pb2.NoteSequence()
    note_sequence.tempos.add().qpm = qpm
    note_sequence.ticks_per_quarter = note_seq.constants.STANDARD_PPQ
    note_sequence.total_time = total_time
    return note_sequence

In [12]:
SAMPLE_RATE = 44100
class CustomTrainer(Trainer):

  def __init__(self, *args, **kwargs):
    super().__init__(*args, **kwargs)

  def evaluation_loop(self,
                      dataloader,
                      description,
                      prediction_loss_only = None,
                      ignore_keys = None,
                      metric_key_prefix = 'eval'):

    eval_output = super().evaluation_loop(dataloader,
                                          description,
                                          prediction_loss_only,
                                          ignore_keys,
                                          metric_key_prefix,)
    if wandb.run is not None:
      input_ids = tokenizer.encode("PIECE_START TIME_SIGNATURE=3_4 GENRE=OTHER TRACK_START INST=0 DENSITY=3 BAR_START NOTE_ON=55 TIME_DELTA=3.9583333333333335 NOTE_OFF=55 TIME_DELTA=0.04166666666666652 NOTE_ON=67 NOTE_ON=63 TIME_DELTA=3.958333333333334 NOTE_OFF=67 NOTE_OFF=63 TIME_DELTA=0.041666666666666075 NOTE_ON=65 NOTE_ON=62 TIME_DELTA=3.958333333333334 NOTE_OFF=65 NOTE_OFF=62 BAR_END BAR_START NOTE_ON=62 NOTE_ON=58 TIME_DELTA=3.9583333333333335 NOTE_OFF=62 NOTE_OFF=58", return_tensors='pt').cuda()
      initial_tokens = model.generate(
          input_ids,
          max_length=512, # changes made here
          do_sample=True,
          temperature=1.7,
          eos_token_id=tokenizer.encode("TRACK_END")[0]
      )
      final_tokens = model.generate(
          initial_tokens,
          max_length=512, # changes made here
          do_sample=True,
          temperature=1.65,
          eos_token_id=tokenizer.encode("TRACK_END")[0]
      )

      token_sequence = tokenizer.decode(final_tokens[0])
      note_sequence = token_sequence_to_note(token_sequence)
      synth = note_seq.fluidsynth
      array_of_floats = synth(note_sequence, sample_rate=SAMPLE_RATE)
      int16_array = note_seq.audio_io.float_samples_to_int16(array_of_floats)
      wandb.log({
          'Generated Audio': wandb.Audio(int16_array, sample_rate=SAMPLE_RATE)
      })

    return eval_output

In [9]:
output_path = 'Final outputs'
steps = 1000
# Configs default and required
config = {
    "output_dir": output_path,
    "num_train_epochs": 20,
    "per_device_train_batch_size": 4,
    "per_device_eval_batch_size": 2,
    "evaluation_strategy": "steps",
    "save_strategy": "steps",
    "eval_steps": steps,
    "logging_steps": steps,
    "logging_first_step": True,
    "save_total_limit": 2,
    "save_steps": steps,
    "lr_scheduler_type": "cosine",
    "learning_rate":5e-5,
    "warmup_ratio": 0.01,
    "weight_decay": 0.01,
    "seed": 1,
    "load_best_model_at_end": True,
    "report_to": "wandb",
    "gradient_accumulation_steps": 1
}

args = Namespace(**config)
args

Namespace(output_dir='Final outputs', num_train_epochs=20, per_device_train_batch_size=4, per_device_eval_batch_size=2, evaluation_strategy='steps', save_strategy='steps', eval_steps=1000, logging_steps=1000, logging_first_step=True, save_total_limit=2, save_steps=1000, lr_scheduler_type='cosine', learning_rate=5e-05, warmup_ratio=0.01, weight_decay=0.01, seed=1, load_best_model_at_end=True, report_to='wandb', gradient_accumulation_steps=1)

In [10]:
train_args = TrainingArguments(**config)
train_args

TrainingArguments(
_n_gpu=1,
accelerator_config={'split_batches': False, 'dispatch_batches': None, 'even_batches': True, 'use_seedable_sampler': True},
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_persistent_workers=False,
dataloader_pin_memory=True,
dataloader_prefetch_factor=None,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=True,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_steps=1000,
evaluation_strategy=IntervalStrategy.STEPS,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
fsdp=[],
fsdp_config={'min_num_params': 0, 'xla': False, 'xla_fsdp_v2': False, 'xla_fsdp_grad_ckpt': False},
fsdp_min_num_params=0,


In [13]:
trainer = CustomTrainer(
    model=model,
    tokenizer=tokenizer,
    args=train_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset['train'],
    eval_dataset=tokenized_dataset['test'],
)

c:\Users\liyak\anaconda3\envs\torch\Lib\site-packages\accelerate\accelerator.py:432: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [17]:
trainer.train()

wandb: Currently logged in as: liyakhatyousuf. Use `wandb login --relogin` to force relogin


  0%|          | 1/12540 [00:00<2:53:22,  1.21it/s]

{'loss': 7.7882, 'grad_norm': 12.045416831970215, 'learning_rate': 3.9682539682539683e-07, 'epoch': 0.0}


  0%|          | 12/12540 [01:14<17:31:00,  5.03s/it]

KeyboardInterrupt: 

In [ ]:
trainer.evaluate()

{'eval_loss': 1.582016110420227,
 'eval_runtime': 22.8102,
 'eval_samples_per_second': 36.694,
 'eval_steps_per_second': 18.369,
 'epoch': 20.0}

In [ ]:
trainer.save_model(output_path)

# Load the Saved model and generate a sample sequence

In [16]:
saved_model = AutoConfig.from_pretrained(output_path)
saved_model

GPT2Config {
  "_name_or_path": "Final outputs",
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": null,
  "embd_pdrop": 0.1,
  "eos_token_id": null,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 512,
  "n_head": 8,
  "n_inner": null,
  "n_layer": 8,
  "n_positions": 2048,
  "pad_token_id": 0,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params": {
    "text-generation": {
      "do_sample": true,
      "max_length": 50
    }
  },
  "torch_dtype": "float32",
  "transformers_version": "4.38.2",
  "use_cache": true,
  "vocab_size": 2052
}

In [14]:
def generate_song_sequence(sample, sr=44100):
  input_ids = tokenizer.encode(sample, return_tensors='pt')
  initial_tokens = GPT2LMHeadModel(saved_model).generate(
      input_ids,
      max_length=256, # changes made here
      do_sample=True,
      temperature=1,
      eos_token_id=tokenizer.encode("TRACK_END")[0]
  )
  final_tokens = GPT2LMHeadModel(saved_model).generate(
      initial_tokens,
      max_length=256, # changes made here
      do_sample=True,
      temperature=1,
      eos_token_id=tokenizer.encode("TRACK_END")[0]
  )
  token_sequence = tokenizer.decode(final_tokens[0],  skip_special_tokens=True)
  note_sequence = token_sequence_to_note(token_sequence)
  synth = note_seq.fluidsynth
  array_of_floats = synth(note_sequence, sample_rate=sr)
  int16_array = note_seq.audio_io.float_samples_to_int16(array_of_floats)
  float32 = int16_array.astype(np.float32)
  return token_sequence, int16_array, float32

In [15]:
def convert_song_to_np(sample, sr=44100):
  original_seq = sample
  original_seq_tokens = token_sequence_to_note(original_seq)
  synth = note_seq.fluidsynth
  array_of_floats = synth(original_seq_tokens, sample_rate=sr)
  int16_array = note_seq.audio_io.float_samples_to_int16(array_of_floats)
  float32 = int16_array.astype(np.float32)
  return int16_array, float32
  # Audio(float32, rate=16000)

## Original Sequence of song

In [19]:
from IPython.display import Audio
import numpy as np
# from pesq import pesq
import soundfile as sf

## Generated Sequence of song

In [16]:
original_numpy, original_float32 = convert_song_to_np('PIECE_START TIME_SIGNATURE=3_4 GENRE=OTHER TRACK_START INST=0 DENSITY=3 BAR_START NOTE_ON=55 TIME_DELTA=3.9583333333333335 NOTE_OFF=55 TIME_DELTA=0.04166666666666652 NOTE_ON=67 NOTE_ON=63 TIME_DELTA=3.958333333333334 NOTE_OFF=67 NOTE_OFF=63 TIME_DELTA=0.041666666666666075 NOTE_ON=65 NOTE_ON=62 TIME_DELTA=3.958333333333334 NOTE_OFF=65 NOTE_OFF=62 BAR_END BAR_START NOTE_ON=62 NOTE_ON=58 TIME_DELTA=3.9583333333333335 NOTE_OFF=62 NOTE_OFF=58 TIME_DELTA=0.04166666666666652 NOTE_ON=60 NOTE_ON=55 TIME_DELTA=3.958333333333334 NOTE_OFF=60 NOTE_OFF=55 TIME_DELTA=0.04166666666666652 NOTE_ON=67 NOTE_ON=63 TIME_DELTA=3.958333333333334 NOTE_OFF=67 NOTE_OFF=63 BAR_END BAR_START NOTE_ON=65 NOTE_ON=62 TIME_DELTA=3.9583333333333335 NOTE_OFF=65 NOTE_OFF=62 TIME_DELTA=0.04166666666666652 NOTE_ON=60 NOTE_ON=55 TIME_DELTA=3.9583333333333335 NOTE_OFF=60 NOTE_OFF=55 TIME_DELTA=0.04166666666666652 NOTE_ON=62 NOTE_ON=58 TIME_DELTA=3.9583333333333335 NOTE_OFF=62 NOTE_OFF=58 BAR_END')
Audio(original_float32, rate=44100)

In [21]:
generated_song_text, generated_numpy, gen_float32 = generate_song_sequence("PIECE_START TIME_SIGNATURE=3_4 GENRE=OTHER TRACK_START INST=41 DENSITY=2 BAR_START TIME_DELTA=2.0 NOTE_ON=55 TIME_DELTA=4.0 NOTE_OFF=55 NOTE_ON=55 TIME_DELTA=4.0 NOTE_OFF=55 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 BAR_END BAR_START TIME_DELTA=2.0 NOTE_ON=57 TIME_DELTA=4.0 NOTE_OFF=57 NOTE_ON=60 TIME_DELTA=4.0 NOTE_OFF=60 NOTE_ON=60")
Audio(gen_float32, rate=44100)

In [ ]:
def save_song_as_wav(int16_array, name="sample", sr=16000):
  # Convert the int16 array back to float32 for saving
  float32_array = int16_array.astype(np.float32) / np.iinfo(np.int16).max

  # Specify the path and filename for the output audio file
  output_audio_path = f'generated/{name}.wav'

  # Save the float32 array as a WAV file
  sf.write(output_audio_path, float32_array, SAMPLE_RATE)

  print(f"Audio saved to {output_audio_path}")

In [ ]:
save_song_as_wav(original_numpy)

Audio saved to /content/drive/MyDrive/MusicGPT/sample.wav


In [ ]:
save_song_as_wav(generated_numpy, "generated_sample")

Audio saved to /content/drive/MyDrive/MusicGPT/generated_sample.wav


## Comparision of original sequence to generated sequence using Audio Quality Metrics PESQ, CER, WER

In [ ]:
ref, rate1 = sf.read('/content/drive/MyDrive/MusicGPT/sample.wav')
deg, rate2 = sf.read('/content/drive/MyDrive/MusicGPT/generated_sample.wav')

# pesq_score = pesq(rate, ref, deg, 'wb')  # 'wb' for wideband, 'nb' for narrowband
# print("PESQ Score:", pesq_score)
print(rate1, ref)
print(rate2, deg)

44100 [0. 0. 0. ... 0. 0. 0.]
44100 [0. 0. 0. ... 0. 0. 0.]


In [ ]:
import librosa as lb

resampled_data_original = lb.resample(original_float32, orig_sr=44100, target_sr=16000)

array([-0.12588635,  0.15371907, -0.1662826 , ...,  2.2058454 ,
       -0.76318526, -1.5254025 ], dtype=float32)

In [ ]:
resampled_data_original.astype(np.float32)

array([-0.12588635,  0.15371907, -0.1662826 , ...,  2.2058454 ,
       -0.76318526, -1.5254025 ], dtype=float32)

In [ ]:
resampled_data_generated = lb.resample(gen_float32, orig_sr=44100, target_sr=16000)
resampled_data_generated

array([ 0.        ,  0.        ,  0.        , ..., -0.1252567 ,
       -0.03066541,  0.11490464], dtype=float32)

In [ ]:
print("PESQ: ", pesq(16000, resampled_data_generated, resampled_data_original, 'wb'))

PESQ:  2.255187511444092


In [ ]:
from jiwer import wer, cer

sample_song = sample
generated_song = generated_song_text

print("Word Error Rate: ", wer(sample_song, generated_song))
print("Character Error Rate: ", cer(sample_song, generated_song))

Word Error Rate:  0.9501607717041801
Character Error Rate:  0.6045673076923077
